In [1]:
%pip install semantic-link-labs
%pip install semantic-link-sempy
%pip install azure-identity azure-keyvault-secrets

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 9, Finished, Available, Finished)

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 699.3/699.3 kB 19.2 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 86.7 MB/s eta 0:00:00:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.1/45.1 kB 18.1 MB/s eta 0:00:00
  Attempting uninstall: semantic-link-sempy
    Found existing installation: semantic-link-sempy 0.9.0
    Not uninstalling semantic-link-sempy at /home/trusted-service-user/cluster-env/trident_env/lib/python3.10/site-packages, outside environment /nfs4/pyenv-78e8f0b4-f751-4e4f-9e7a-d904e5476fd6
    Can't uninstall 'semantic-link-sempy'. No files were found to uninstall.

[notice] A new release of pip is available: 23.1.2 -> 25.1
[notice] To update, run: python -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 23.1.2 -> 25.1
[notice] To update, run: python -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, coalesce, current_date
from delta.tables import DeltaTable
import json
import pandas as pd
import requests
import concurrent.futures
import time
import msal
import datetime

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 11, Finished, Available, Finished)

In [3]:
import sempy_labs as labs
from sempy_labs import migration, directlake, admin, graph, vertipaq_analyzer
from sempy_labs import lakehouse as lake
from sempy_labs import report as rep
from sempy_labs.tom import connect_semantic_model
from sempy_labs.report import ReportWrapper
import sempy
sempy.fabric._client._utils._init_analysis_services()
import Microsoft.AnalysisServices.Tabular as TOM


StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 12, Finished, Available, Finished)

In [4]:
#Reading the Datafrom the delta file
workspacess_df = (
    spark.read.format("delta")
    .load("abfss://d3120490-76ae-4ef4-a440-2bd65732ccdc@onelake.dfs.fabric.microsoft.com/fecab367-5d3a-41c1-8037-7801192932ba/Tables/fabric_workpsaces")
)

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 13, Finished, Available, Finished)

In [5]:
#Filter Workspaces for a capactity
filtered_workspaces_df = workspacess_df.filter(col("capacityId") == "76F4499E-05FF-44A9-8C2F-323EE14EA1A7")
workspaceIds_list = [row["id"] for row in filtered_workspaces_df.select("id").collect()]

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 14, Finished, Available, Finished)

In [6]:
#Reading the Datafrom the delta file
datasets_df = (
    spark.read.format("delta")
    .load("abfss://d3120490-76ae-4ef4-a440-2bd65732ccdc@onelake.dfs.fabric.microsoft.com/fecab367-5d3a-41c1-8037-7801192932ba/Tables/datasets")
)

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 15, Finished, Available, Finished)

In [7]:
#Filter Datsets for a capactity
filtered_datasets_df = datasets_df.filter(col("workspaceId").isin(workspaceIds_list))

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 16, Finished, Available, Finished)

In [8]:
def run_vertipaq_analyzer(Dataset_Id, Workspace_Id):
    # Run VertiPaq analyzer
    vertipaq_results = vertipaq_analyzer(dataset=Dataset_Id, workspace=Workspace_Id)

    # Combine all result sections into a single DataFrame and tag with their __Source__
    result_df = pd.concat(
        [df.assign(__Source__=key) for key, df in vertipaq_results.items()],
        ignore_index=True
    )

    # Extract dataset-level details
    dataset_details_df = (
        result_df[result_df["Dataset Name"].notna()]
        [["Dataset Name", "Total Size", "Column Count", "Table Count", "Default Mode"]]
        .assign(**{"Dataset Id": Dataset_Id})
        .reset_index(drop=True)
    )

    # Extract table-level details where source is "Tables"
    table_columns_to_keep = [
        "Total Size", "__Source__", "Table Name", "Type", "Row Count", "Dictionary Size",
        "Data Size", "Hierarchy Size", "Relationship Size", "Partitions", "Columns", "% DB"
    ]

    dataset_table_details_df = (
        result_df[result_df["__Source__"] == "Tables"]
        [table_columns_to_keep]
        .assign(**{"Dataset Id": Dataset_Id})
        .reset_index(drop=True)
    )

    return dataset_details_df, dataset_table_details_df




StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 17, Finished, Available, Finished)

In [9]:
# Define empty DataFrames to accumulate results
dataset_details_df = pd.DataFrame()
dataset_table_details_df = pd.DataFrame()

# Loop with error handling
for row in filtered_datasets_df.toLocalIterator():
    try:
        temp_dataset_details_df, temp_dataset_table_details_df = run_vertipaq_analyzer(
            row["id"], row["workspaceId"]
        )

        if not temp_dataset_details_df.empty:
            dataset_details_df = pd.concat(
                [dataset_details_df, temp_dataset_details_df],
                ignore_index=True
            )
        else:
            print(f"No dataset-level data for: workspaceId={row['workspaceId']}, id={row['id']}")

        if not temp_dataset_table_details_df.empty:
            dataset_table_details_df = pd.concat(
                [dataset_table_details_df, temp_dataset_table_details_df],
                ignore_index=True
            )
        else:
            print(f"No table-level data for: workspaceId={row['workspaceId']}, id={row['id']}")

    except Exception as e:
        print(f"Error processing workspaceId={row['workspaceId']}, id={row['id']}: {e}")

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 18, Finished, Available, Finished)

Error processing workspaceId=228db8e8-6203-4ba8-b406-7b1da29c34c1, id=c8644a57-877e-4b30-8845-de401b0e75ec: The '<euii>Akhil.Grandhi@tvsmotor.com</euii>' user does not have permission to call the Discover method.

   at Microsoft.AnalysisServices.XmlaClient.CheckForSoapFault(XmlReader reader, XmlaResult xmlaResult, Boolean throwIfError)
   at Microsoft.AnalysisServices.XmlaClient.CheckForError(XmlReader reader, XmlaResult xmlaResult, Boolean throwIfError)
   at Microsoft.AnalysisServices.XmlaClient.SendMessage(Boolean endReceivalIfException, Boolean readSession, Boolean readNamespaceCompatibility)
   at Microsoft.AnalysisServices.Core.AnalysisServicesClient.Discover(IMajorObject obj, ObjectExpansion expansion, JaXmlSerializer serializer)
   at Microsoft.AnalysisServices.Core.Server.Refresh(IMajorObject obj, ObjectExpansion expansion)
   at Microsoft.AnalysisServices.Core.Server.SendRefresh(IMajorObject obj, ObjectExpansion expansion)
   at Microsoft.AnalysisServices.MajorObject.Refresh

Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=4155dc0a-cce4-4f24-b85a-453bf47bf308: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=d351cc98-9b65-48cc-bf8c-d2515ea615aa: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.


Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=8b4f3bd9-f657-4761-b693-1fd0069c0997: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=bdbcab5e-a405-41ef-8fad-3ca43fa736af: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=644f2d46-03a5-41cd-bb50-3fddc8205654: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=4de14197-8344-4d1f-b588-0ec224bf324b: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=507b9d28-12cb-4f75-8628-ed804ca738d1: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=7a0f5e7f-9540-4c4d-bdd7-cce58da46d97: 🔴 

Error processing workspaceId=831affc2-2227-42e3-ac1d-a7a2dd1e9756, id=b85f5603-6c40-48ce-9e7b-6c28579e29a3: 🔴 The 'b85f5603-6c40-48ce-9e7b-6c28579e29a3' item was not found in the 'Domestic 2W Marketing - CXO' workspace.
Error processing workspaceId=831affc2-2227-42e3-ac1d-a7a2dd1e9756, id=b61d3df0-6a0c-4c18-b9f9-18fcde68a5f9: The '<euii>Akhil.Grandhi@tvsmotor.com</euii>' user does not have permission to call the Discover method.

   at Microsoft.AnalysisServices.XmlaClient.CheckForSoapFault(XmlReader reader, XmlaResult xmlaResult, Boolean throwIfError)
   at Microsoft.AnalysisServices.XmlaClient.SendMessage(Boolean endReceivalIfException, Boolean readSession, Boolean readNamespaceCompatibility)
   at Microsoft.AnalysisServices.Core.AnalysisServicesClient.Discover(IMajorObject obj, ObjectExpansion expansion, JaXmlSerializer serializer)
   at Microsoft.AnalysisServices.Core.Server.Refresh(IMajorObject obj, ObjectExpansion expansion)
   at Microsoft.AnalysisServices.MajorObject.Refresh(Ob

Error processing workspaceId=4bc02dfe-903e-445c-b724-3b974bcd0658, id=d74a22ac-cad0-4d27-98ec-ff433f1c4652: 🔴 The '4bc02dfe-903e-445c-b724-3b974bcd0658' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=b3e6b637-eb7a-4361-825e-e36672680d95: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=a295bad5-9850-4ac7-8f7a-d46b848f8f00: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.
Error processing workspaceId=ac8a466e-cbd2-4c73-9b6e-3b18cded7ee8, id=55566213-2dae-4d4a-a067-f22334ab9afe: 🔴 The 'ac8a466e-cbd2-4c73-9b6e-3b18cded7ee8' workspace was not found.


Error processing workspaceId=4bc02dfe-903e-445c-b724-3b974bcd0658, id=44c95695-b603-4ea7-9c89-b56a6dbc24dc: 🔴 The '4bc02dfe-903e-445c-b724-3b974bcd0658' workspace was not found.


Error processing workspaceId=ac8a466e-cbd2-4c73-9b6e-3b18cded7ee8, id=a1394573-4728-479b-a9e7-e55c4299da27: 🔴 The 'ac8a466e-cbd2-4c73-9b6e-3b18cded7ee8' workspace was not found.
Error processing workspaceId=762cdec9-ca96-4a30-a5c3-c94a3a4a8e4a, id=1670589a-5623-4bda-b732-9ecc1f2a32ca: 🔴 The '762cdec9-ca96-4a30-a5c3-c94a3a4a8e4a' workspace was not found.
Error processing workspaceId=faa61b04-f0c0-4e77-b206-beaf9d93208e, id=c691559d-d050-4f18-977e-af82eabc26d6: 🔴 The 'faa61b04-f0c0-4e77-b206-beaf9d93208e' workspace was not found.


Error processing workspaceId=831affc2-2227-42e3-ac1d-a7a2dd1e9756, id=5e2b04a2-6366-4878-be47-f5721326197b: 🔴 The '5e2b04a2-6366-4878-be47-f5721326197b' item was not found in the 'Domestic 2W Marketing - CXO' workspace.


In [10]:
dataset_details_df.columns = dataset_details_df.columns.str.replace(' ', '', regex=False)
dataset_table_details_df.columns = dataset_table_details_df.columns.str.replace(' ', '', regex=False)

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 19, Finished, Available, Finished)

In [11]:
spark_dataset_details_df = spark.createDataFrame(dataset_details_df)

# Overwrite the Delta table with the updated DataFrame
spark_dataset_details_df.write.format("delta").mode("overwrite").saveAsTable("datasets_vertipaq_details_01")


StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 20, Finished, Available, Finished)

In [12]:
spark_dataset_table_details_df = spark.createDataFrame(dataset_table_details_df)
# Overwrite the Delta table with the updated DataFrame
spark_dataset_table_details_df.write.format("delta").mode("overwrite").saveAsTable("datasets_tables_vertipaq_details_01")

StatementMeta(, 99d68436-e0c5-4f0b-8e81-728f4b7e4452, 21, Finished, Available, Finished)